# Get Tweets in Real Time using Twitter API

We are using Tweepy library to route all the Live tweets to a TCP socket server.<br> 
This server is hosted in Local Machine.

Import tweepy library

In [2]:
import tweepy

Import OAuthHandler.<br> It is used for Authentication protocol (OAuth) of Twitter API.

In [3]:
from tweepy import OAuthHandler

Import Stream & StreamListner.<br> This actually listen to streaming data getting from the socket.

In [4]:
from tweepy import Stream
from tweepy.streaming import StreamListener

Import socket. It is used to create socket connection with Localhost i.e. local server. <br>
Json is used because twitter data comes in json format.

In [5]:
import socket
import json

To connect to Twitter API, we need these 4 Keys. <br>
It can be generated from https://apps.twitter.com/ by creating a new app.

In [6]:
consumer_key = '******************'
consumer_secret = '*************************'
access_token = '**************************************'
access_secret = '***********************************************'

#### Class TweetsListner
    1.It is listening to the stream via StreamListener. 
    2.constrctor function (init) : initializing the socket. 
    3.data contains the tweets json coming from the stream. 
    4.In this json object field 'text' contains the actual Tweet.
    5.The actual tweet is extracted & sent to the client socket.
    6.Error handling is done to catch & throw errors.

In [7]:
class TweetsListener(StreamListener):
  def __init__(self, csocket):
      self.client_socket = csocket
  def on_data(self, data):
      try:
          msg = json.loads( data )
          print( msg['text'].encode('utf-8') )
          self.client_socket.send( msg['text'].encode('utf-8') )
          return True
      except BaseException as e:
          print("Error on_data: %s" % str(e))
      return True
  def on_error(self, status):
      print(status)
      return True

### Function SendData():
    1. auth is doing Authentication check using OAuthHandler. It uses 4 keys of Twitter APIs.
    2. consumer_key & consumer_secret are like username & access_token & access_secret are like password.
    3. twitter_stream will get the actual twitter live stream data.
    4. It'll call Stream with auth & call the Class TweetsListner & pass c_socket info to the class.
    5. From the stream of tweets, filter & take only tweets which contains "Trump" word.

In [8]:
def sendData(c_socket):
  auth = OAuthHandler(consumer_key, consumer_secret)
  auth.set_access_token(access_token, access_secret)
  twitter_stream = Stream(auth, TweetsListener(c_socket))
  twitter_stream.filter(track=['trump'])

### Socket Creation:
    1. Socket is created by using socket function.
    2. Host is localhost, which in our case is IP of Cloudxlab, where this Jupyter notebook is running.
    3. Port is 5555 (It can be anything, unique for this service)
    4. Now bind host & port address to the socket.

In [10]:
s = socket.socket()         # Create a socket object
host = "192.168.56.1"       # Get local machine name
port = 5555                 # Reserve a port for your service.
s.bind((host, port))        # Bind to the port
print("Listening on port: %s" % str(port))

Listening on port: 5555


socket will wait & listen for few seconds. <br>
After that connection is made.

In [11]:
s.listen(5)                 # Now wait for client connection.
c, addr = s.accept()        # Establish connection with client.
print( "Received request from: " + str( addr ) )

Received request from: ('192.168.56.1', 49661)


### Send live Tweets in real time to the Socket
Function sendData will send all the Tweets containing word 'Trump' to socket 'c' in real time.<br>
This will be consumed in the next code of Spark Streaming to do Trend Analysis.

In [12]:
sendData( c )

b"RT @anneapplebaum: Do a thought experiment: if Biden were sick, what would happen? Here's my guess: Trump would be openly gloating, Republi\xe2\x80\xa6"
b'RT @ByMikeBaker: Updated list of coronavirus infections in and around the White House:\n\xe2\x80\xa2 POTUS\n\xe2\x80\xa2 FLOTUS\n\xe2\x80\xa2 Trump adviser Hope Hicks\n\xe2\x80\xa2 Kellya\xe2\x80\xa6'
b"RT @SeanKGriffiths: Hearing reports that Kanye West has turned up at President Trump's bedside with a fishing rod and a whole rotisserie ch\xe2\x80\xa6"
b'RT @markberman: I\xe2\x80\x99m honest to god struck seeing *current Secret Service agents* ripshit about the *sitting president* because they feel he\xe2\x80\xa6'
b'RT @MZHemingway: Biden Lead Over Trump Cut To 3 Points After Presidential Debate: IBD/TIPP Poll https://t.co/DJtQ9NtYUC via @IBDinvestors'
b'H\xc3\xa1 quem diga que Covid pode melhorar imagem de Trump - https://t.co/22qnhp5P48'
b'RT @kellyblaus: As we watch Trump recover from COVID-19, please remember that he will have

Error on_data: 'text'
b'RT @mmpadellan: I think Joe Biden should NOT stop campaigning just because trump was stupid enough not to follow COVID-19 guidelines and "c\xe2\x80\xa6'
b'RT @davitydave: It appears that a lot of people who attended Amy Coney Barrett\xe2\x80\x99s SCOTUS announcement event at the Rose Garden are positive.\xe2\x80\xa6'
b'\xe4\xbb\xae\xe7\x97\x85\xe3\x81\xa3\xe3\x81\xa6\xe3\x81\x8b\xe2\x80\xa6\xe2\x80\xa6\xe3\x81\xbe\xe3\x81\x82\xe3\x82\x84\xe3\x82\x8a\xe3\x81\x8b\xe3\x81\xad\xe3\x82\x93\xe3\x81\xaa\xe3\x80\x81\xe3\x81\x82\xe3\x81\xae\xe3\x80\x8c\xe8\x8a\xb1\xe6\x9c\xad\xe9\x87\x8e\xe9\x83\x8e\xf0\x9f\x8e\xb4\xe3\x80\x8d\xe3\x81\xa0\xe3\x81\xa3\xe3\x81\x9f\xe3\x82\x89\xf0\x9f\x98\x82\n\n\xe3\x83\x9e\xe3\x82\xa4\xe3\x82\xb1\xe3\x83\xab\xe3\x83\xbb\xe3\x83\xa0\xe3\x83\xbc\xe3\x82\xa2\xe7\x9b\xa3\xe7\x9d\xa3\xe3\x80\x81\xe3\x83\x88\xe3\x83\xa9\xe3\x83\xb3\xe3\x83\x97\xe6\xb0\x8f\xe3\x81\xaf\xe3\x80\x8c\xe3\x83\x97\xe3\x83\xad\xe3\x81\xae\xe5\x98\x98\xe3\x81\xa4\xe3\x8

b'I wonder if we\xe2\x80\x99re still going to have people not wear masks if the Rona gets Trump'
b'RT @glennkirschner2: So Donald Trump has cancelled everything on his calendar, is sitting around w/a low grade fever &amp; a fully charged cell\xe2\x80\xa6'
b'RT @NoqReport: Few things are more disgusting than trying to cash in on a relationship by betraying trust.\n\nThat\xe2\x80\x99s what Stephanie Winston W\xe2\x80\xa6'
b'@benshapiro Huh? #Hypocrisy \n\nhttps://t.co/wSZnXNPzEj'
b'\xe2\x80\x9cWhen people who differ politically still show empathy for each other \xe2\x9d\xa4\xef\xb8\x8f\xe2\x9d\xa4\xef\xb8\x8f\xe2\x80\x9d \xe2\x80\x94Joanne83637, loving mother, wife, stan\xe2\x80\xa6 https://t.co/MbuDYD4aO4'
b'RT @BernieSanders: We will not have a normal economy or educational system unless we effectively address the COVID-19 pandemic.\n\nWe will no\xe2\x80\xa6'
b'RT @girlsreallyrule: Donald Trump is receiving cutting edge medical treatment, that will bill out in the thousands, despite on

b'RT @jeremyslevin: .@IlhanMN gets *actual death threats* on this platform all the time and Twitter doesn\xe2\x80\x99t do shit https://t.co/tFeyDq9UXC'
b'RT @lyricistkai: woah hearing jungkook saying fuck yesterday, trump getting covid, txt and runaway suddenly trending and txt coming back on\xe2\x80\xa6'
b'RT @dsfashl: @TheDCPolitics It remains interesting that Herman Cain\xe2\x80\x99s death from COVID-19\xe2\x80\x94after he attended a Trump rally in Oklahoma\xe2\x80\x94didn\xe2\x80\x99\xe2\x80\xa6'
b'RT @MatthewBevan: 4 years ago exactly Hillary Clinton had pneumonia'
b'RT @kevunn: Trump: I tested positive.\n\nThe IRS:'
b'Move over #BunkerBoyTrump'
b"Despite Trump's condition, ideology and propaganda continues to transcend evidence and facts - endangering more staff."
b'By ignoring the Trump COVID topic today, I find myself highly productive with ideas to take down CCP. We didn\xe2\x80\x99t ago\xe2\x80\xa6 https://t.co/xSxDnK9XgY'
b'RT @BernerSanders: Just a reminder that we are payi

b"RT @AwakenedOutlaw: @JPinVanCity88 @realDonaldTrump @prayingmedic Yo, JP.  Can you explain to me how Trump is responsible for Dem Gov's sen\xe2\x80\xa6"
b'RT @DeAnna4Congress: Could Trump catching COVID-19 technically be viewed as an assassination attempt on our President by the Chinese?'
b'Being any Trump Appointee is a dubious honour and in recent days a dangerous one as well!'
b"RT @MCRRViper: @QTAnon1 It's getting beyond the coincidence stage.\n\nWhat are we at now, about a half dozen members of President Trump's par\xe2\x80\xa6"
b"RT @JudLounsbury: I'm happy ## something ## prevented Trump from having super spreader events in Wisconsin.  Lives have been saved."
b'RT @TakeAShilllPill: Trump supporters realizing corona is actually real.'
b'@MiamiHerald @nytmike @DMRegister @BostonGlobe @latimes @SenateDems @Comey @JohnBerman @DavidJollyFL @NPR @CNN\xe2\x80\xa6 https://t.co/nx5kq6l8Vy'
b'RT @BernerSanders: Just a reminder that we are paying for Trump\xe2\x80\x99s healthcare as he g

...

b'RT @gtconway3d: I can relate'
b'RT @charliekirk11: We are watching an activist media and political base wish death upon Trump. Never forget this.'
b'S\xc3\xb3 lembrando que o mundo dele inclui, basicamente, os que pensam como ele...'
b'RT @PreetBharara: In a million years would Trump suspend his campaign if the situation were reversed? No, he would mock Biden, blame Biden\xe2\x80\xa6'
b'RT @SteveSchmidtSES: Gettysburg, Normandy and the Edmund Pettus Bridge. Trump has lied to the country on more than 25,000 occasions, assaul\xe2\x80\xa6'
b'RT @SteveSchmidtSES: .@ProjectLincoln We are hearing from many sources within the Trump campaign about the fear and panic in the ranks. Sta\xe2\x80\xa6'
b"RT @ChrisRulon: That's Mike Wallace(Chris's father) in between Trump and Maxwell in that picture. They all come from the same rotten world\xe2\x80\xa6"
b'RT @appistol: \xce\x9f\xce\xb9 radical left \xce\xb3\xcf\x81\xce\xac\xcf\x86\xce\xbf\xcf\x85\xce\xbd \xce\xb1\xce\xaf\xcf\x83\xcf\x87\xce\xb7 \x

b'RT @Milliganreports: This by @AssociatedPress has got to be one of the defining photographs of the age (and, as it happens, @theage). Trump\xe2\x80\xa6'
b'RT @matthewjdowd: The reason why the Trump campaign is not pulling its negative ads, as the Biden campaign already did earlier, is because\xe2\x80\xa6'
b'Dear American Left,\n\nWishing death on Trump just helps his cause. No wonder he and the Republican party are killing\xe2\x80\xa6 https://t.co/bwiLS2Fp61'
b'RT @lemondefr: Covid-19 : l\xe2\x80\x99hospitalisation de Donald Trump chamboule la pr\xc3\xa9sidentielle am\xc3\xa9ricaine https://t.co/FMqPBQfgE0'
b'RT @GarciaRosalind: My daughter said she resented the fact that taxpayers are paying for @realDonaldTrump \xe2\x80\x99s best in the world healthcare,\xe2\x80\xa6'
b'RT @RodneyCaston: Trump chose to risk the lives of everyone around him instead of telling Americans he was infected with COVID19 days ago.'
b"RT @Eleven_Films: **NEW VIDEO**\n\nBREAKING: 95 Minutes In Trump's America

b'RT @emirrhany: Ne \xc3\xa7abuk haber al\xc4\xb1yosunuz ya #Trump https://t.co/3h2YoZ4O9k'
b'RT @jordanzakarin: To help Donald Trump get the full COVID-19 experience, let\xe2\x80\x99s make sure he loses his job and is evicted from his home nex\xe2\x80\xa6'
b'RT @JustSchmeltzer: If I am @JoeBiden, I am using this moment, when people are nervously watching the news a lot, to buy 30 mins on network\xe2\x80\xa6'
b'@realDonaldTrump WE LOVE YOU, WE LOVE YOU, WE LOVE YOU PRESIDENT TRUMP!!!'
b'There really is no limits for these idiots'
b'RT @NatSecLisa: It\xe2\x80\x99s interesting that Amy Coney Barrett can be publicly opposed to Roe v. Wade and say that her personal beliefs wouldn\xe2\x80\x99t i\xe2\x80\xa6'
b'RT @MollyJongFast: Nice to see Matt Gaetz with the dumbest take of the evening'
b'RT @TheTweetOfGod: Keeping six feet away from Donald Trump has been good health advice since 1946.'
b'RT @BernerSanders: Just a reminder that we are paying for Trump\xe2\x80\x99s healthcare as he gets CO

b'RT @jondharvey: 1/ I wondered when something might happen like this (@TheDailyShow doing @MrMichaelSpicer style skits). A similar thing hap\xe2\x80\xa6'
b'RT @Adorable_Todd: Donald Trump has gained over 1.2 Million followers in the last day!'
b'RT @GKeile: Amy Coney Barrett already had COVID a while back so the media can quit talking about Trump or one of the republicans possibly g\xe2\x80\xa6'
b'RT @jack_hikuma: \xe7\x84\xa1\xe4\xba\x8b\xe3\x81\xab\xe6\x88\xbb\xe3\x81\xa3\xe3\x81\xa6\xe3\x81\x8d\xe3\x81\xa6\xe3\x81\x8f\xe3\x82\x8c\xe3\x83\xbc\xf0\x9f\x99\x8fTRUMP\xe5\x85\x84\xe8\xb2\xb4\xf0\x9f\x92\xaa\xf0\x9f\x92\xaa\xf0\x9f\x87\xba\xf0\x9f\x87\xb8\xf0\x9f\x87\xba\xf0\x9f\x87\xb8\n\xe4\xb8\x96\xe7\x95\x8c\xe4\xb8\xad\xe3\x81\x8c\xe3\x81\x82\xe3\x81\xaa\xe3\x81\x9f\xe3\x81\xae\xe5\xbe\xa9\xe6\xb4\xbb\xe3\x82\x92\xe7\xa5\x88\xe3\x81\xa3\xe3\x81\xa6\xe3\x81\x84\xe3\x82\x8b\xf0\x9f\x99\x8f\n46\xe4\xbb\xa3\xe3\x82\xa2\xe3\x83\xa1\xe3\x83\xaa\xe3\x82\xab\xe5\x90\x88\xe8\xa1\x86\xe5\x9b\x

ProtocolError: ('Connection broken: IncompleteRead(0 bytes read)', IncompleteRead(0 bytes read))